<a href="https://colab.research.google.com/github/Juxlarry/LLM-Engineering-Mastering-AI-Large-Language-Models-LLMs-/blob/main/Gradio1.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [ ]:
%pip install anthropic

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 325.2/325.2 kB 10.6 MB/s eta 0:00:00


In [ ]:
import os
import requests
from bs4 import BeautifulSoup
from typing import List
from dotenv import load_dotenv
from openai import OpenAI
import google.generativeai as genai
import anthropic
import gradio as gr
from google.colab import userdata

In [ ]:
load_dotenv()
os.environ["OPENAI_API_KEY"] = userdata.get('OpenAI')
os.environ["GEMINI_API"] = userdata.get('GEMINI_API')

In [ ]:
openai = OpenAI(api_key=userdata.get('OpenAI'))
# openai = OpenAI()
claude = anthropic.Anthropic()
genai.configure(api_key=userdata.get('GEMINI_API'))
# google.generativeai.configure()

In [ ]:
system_message= "You are a helpful assistant."

In [ ]:
def message_gpt(prompt):
  messages = [
      {"role": "system", "content": system_message},
      {"role": "user", "content": prompt}
  ]
  completion = openai.chat.completions.create(
      model="gpt-3.5-turbo",
      messages=messages
  )
  print(f"Model used: gpt-3.5-turbo")
  print(f"Role - {completion.choices[0].message.role}")
  print(f"To_JSON: \n {completion.choices[0].message.to_json}")

  # Check what attributes are available
  # print(f"Available attributes: {dir(completion.choices[0].message)}")

  return completion.choices[0].message.content


In [ ]:
# def stream_gpt(prompt):
#   messages = [
#       {"role": "system", "content": system_message},
#       {"role": "user", "content": prompt}
#   ]
#   stream = openai.chat.completions.create(
#       model="gpt-3.5-turbo",
#       messages=messages,
#       stream = True
#   )
#   print(f"Model used: gpt-3.5-turbo")
#   print(f"Role - {stream.choices[0].delta.Role}")
#   print(f"To_JSON: \n {stream.choices[0].delta.to_json}")

#   # Check what attributes are available
#   print(f"Available attributes: {dir(stream.choices[0].delta)}")

#   result = ""
#   for chunk in stream:
#     result += chunk.choices[0].delta.content or ""
#     yield result


def stream_gpt(prompt):
    messages = [
        {"role": "system", "content": system_message},
        {"role": "user", "content": prompt}
    ]

    try:
        stream = openai.chat.completions.create(
            model="gpt-3.5-turbo",
            messages=messages,
            stream=True
        )

        print(f"Model used: gpt-3.5-turbo")

        result = ""
        chunk_count = 0

        for chunk in stream:
            chunk_count += 1

            # Debug first few chunks
            if chunk_count <= 3:
                print(f"\n--- Chunk {chunk_count} ---")
                print(f"Chunk: {chunk}")
                if chunk.choices:
                    delta = chunk.choices[0].delta
                    print(f"Delta content: {getattr(delta, 'content', None)}")
                    print(f"Delta role: {getattr(delta, 'role', None)}")
                    print(f"Finish reason: {getattr(chunk.choices[0], 'finish_reason', None)}")

            # Extract and accumulate content
            if chunk.choices and hasattr(chunk.choices[0].delta, 'content'):
                content = chunk.choices[0].delta.content
                if content:  # content can be None
                    result += content
                    yield result

        print(f"\nTotal chunks processed: {chunk_count}")

    except Exception as e:
        print(f"Error in streaming: {e}")
        yield f"Error: {e}"

In [ ]:
def message_gemini(prompt):
    """
    Simple function to send a prompt to Gemini and get response
    """
    try:
        # Initialize the model
        model = genai.GenerativeModel(
            model_name="gemini-1.5-flash",  # or "gemini-1.5-pro"
            system_instruction=system_message
        )

        # Generate response
        response = model.generate_content(prompt, stream=True)

        print(f"Model used: gemini-1.5-flash")
        # print(f"Response: {response.text}")

        result = ""
        for chunk in response:
            if chunk.text:
                result += chunk.text
                print(f"Chunk: {chunk.text}")  # Debug: show each chunk
                yield result

        print(f"Final result: {result}")

        # return response.text


    except Exception as e:
        print(f"Error with Gemini: {e}")
        return None

In [ ]:
# Option 2: Using OpenAI-compatible interface (if you have that setup)
gemini_client = OpenAI(api_key=userdata.get('GEMINI_API'), base_url="https://generativelanguage.googleapis.com/v1beta/openai/")

def message_gemini_openai_style(prompt):
    """
    If you're using Gemini through an OpenAI-compatible API
    """
    # Assuming you have gemini_client configured similar to openai client
    try:
      messages = [
          {"role": "system", "content": system_message},
          {"role": "user", "content": prompt}
      ]

      completion = gemini_client.chat.completions.create(
          model="gemini-1.5-flash",
          messages=messages,
          stream= True
      )

      result = ""
      for chunk in completion:
          if chunk.choices[0].delta.content:
              content = chunk.choices[0].delta.content
              result += content
              yield result

    except Exception as e:
        print(f"Error with Gemini OpenAI-style streaming: {e}")
        yield f"Error: {e}"

In [ ]:
message_gpt("What is coding")

Model used: gpt-3.5-turbo
Role - assistant
To_JSON: 
 <bound method BaseModel.to_json of ChatCompletionMessage(content="Coding, also known as programming, is the process of writing instructions for a computer to follow in order to perform a certain task. It involves creating sets of commands using a specific programming language, which the computer can understand and execute. Coding is used to develop software, websites, apps, and other digital products. It is an essential skill in today's technology-driven world.", refusal=None, role='assistant', annotations=[], audio=None, function_call=None, tool_calls=None)>
Role: assistant
Content: Coding, also known as programming, is the process of writing instructions for a computer to follow in order to perform a certain task. It involves creating sets of commands using a specific programming language, which the computer can understand and execute. Coding is used to develop software, websites, apps, and other digital products. It is an essenti

"Coding, also known as programming, is the process of writing instructions for a computer to follow in order to perform a certain task. It involves creating sets of commands using a specific programming language, which the computer can understand and execute. Coding is used to develop software, websites, apps, and other digital products. It is an essential skill in today's technology-driven world."

In [ ]:
view = gr.Interface(
    fn=message_gpt,
    inputs=[gr.Textbox(label="Your Message:", lines=4)],
    outputs= [gr.Markdown(label="Response:", lines=8)],
    allow_flagging="never"
    )

view.launch(share=True,debug=True)

/usr/local/lib/python3.12/dist-packages/gradio/interface.py:415: UserWarning: The `allow_flagging` parameter in `Interface` is deprecated. Use `flagging_mode` instead.
  warnings.warn(


Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://af23d9a333d5714c45.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Model used: gpt-3.5-turbo
Role - assistant
To_JSON: 
 <bound method BaseModel.to_json of ChatCompletionMessage(content='Coding refers to the process of designing and creating instructions that a computer can understand and execute. It involves using programming languages to write code that tells a computer how to perform specific tasks or functions. Coders use coding languages like Python, Java, JavaScript, and others to develop websites, software, applications, and various other digital products. Coding is an essential skill for computer programming and software development.', refusal=None, role='assistant', annotations=[], audio=None, function_call=None, tool_calls=None)>
Available attributes: ['__abstractmethods__', '__annotations__', '__class__', '__class_getitem__', '__class_vars__', '__copy__', '__deepcopy__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__fields__', '__fields_set__', '__format__', '__ge__', '__get_pydantic_core_schema__', '__get_pydantic_json_sche

In [ ]:
view = gr.Interface(
    fn=stream_gpt,
    inputs=[gr.Textbox(label="Your Message:", lines=4)],
    outputs= [gr.Markdown(label="Response:")],
    allow_flagging="never"
    )

view.launch(share=True,debug=True)

/usr/local/lib/python3.12/dist-packages/gradio/interface.py:415: UserWarning: The `allow_flagging` parameter in `Interface` is deprecated. Use `flagging_mode` instead.
  warnings.warn(


Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://d793a278b9249781ea.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Model used: gpt-3.5-turbo

--- Chunk 1 ---
Chunk: ChatCompletionChunk(id='chatcmpl-CJ8X7OkjydvZtx1py9lrGOwAXAG1Y', choices=[Choice(delta=ChoiceDelta(content='', function_call=None, refusal=None, role='assistant', tool_calls=None), finish_reason=None, index=0, logprobs=None)], created=1758677069, model='gpt-3.5-turbo-0125', object='chat.completion.chunk', service_tier='default', system_fingerprint=None, usage=None, obfuscation='bYNOd')
Delta content: 
Delta role: assistant
Finish reason: None

--- Chunk 2 ---
Chunk: ChatCompletionChunk(id='chatcmpl-CJ8X7OkjydvZtx1py9lrGOwAXAG1Y', choices=[Choice(delta=ChoiceDelta(content='Coding', function_call=None, refusal=None, role=None, tool_calls=None), finish_reason=None, index=0, logprobs=None)], created=1758677069, model='gpt-3.5-turbo-0125', object='chat.completion.chunk', service_tier='default', system_fingerprint=None, usage=None, obfuscation='I')
Delta content: Coding
Delta role: None
Finish reason: None

--- Chunk 3 ---
Chunk: ChatCompleti

In [ ]:
view = gr.Interface(
    fn=message_gemini,
    inputs=[gr.Textbox(label="Your Message:", lines=4)],
    outputs= [gr.Markdown(label="Response:")],
    allow_flagging="never"
    )

view.launch(share=True,debug=True)

/usr/local/lib/python3.12/dist-packages/gradio/interface.py:415: UserWarning: The `allow_flagging` parameter in `Interface` is deprecated. Use `flagging_mode` instead.
  warnings.warn(


Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://4406bc4751b405623b.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Model used: gemini-1.5-flash
Chunk: Coding
Chunk:  is the process of using a programming language to give instructions to a computer.  
Chunk: These instructions tell the computer what actions to perform, what data to process, and
Chunk:  how to display or store the results.  Essentially, it's like writing a recipe for a computer, but instead of baking a cake, you're
Chunk:  creating a program, website, app, or other software.

Think of it this way:  computers only understand a very basic language of 0s and
Chunk:  1s (binary).  Coding provides a way for humans to translate their ideas and instructions into a form the computer can understand.  Programming languages act as the bridge between human-readable instructions and the computer's binary language.


Chunk: Coding involves several key aspects:

* **Syntax:** This refers to the specific rules and structure of a programming language.  Just like grammar in English, incorrect syntax will result in errors.
* **Logic:**  This is crucial

In [ ]:
view = gr.Interface(
    fn=message_gemini_openai_style,
    inputs=[gr.Textbox(label="Your Message:", lines=4)],
    outputs= [gr.Markdown(label="Response:")],
    allow_flagging="never"
    )

view.launch(share=True,debug=True)

/usr/local/lib/python3.12/dist-packages/gradio/interface.py:415: UserWarning: The `allow_flagging` parameter in `Interface` is deprecated. Use `flagging_mode` instead.
  warnings.warn(


Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://8ba114523c2d3b4a3e.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Keyboard interruption in main thread... closing server.
Killing tunnel 127.0.0.1:7861 <> https://8ba114523c2d3b4a3e.gradio.live


In [ ]:
def stream_mode(prompt, model):
  if model == "GPT":
    result = message_gpt(prompt)
  elif model == "GPT-Stream":
    result = message_gemini(prompt)
  elif model == "Gemini":
    result = message_gemini(prompt)
  elif model == "Gemini-OpenAI":
    result = message_gemini_openai_style(prompt)
  else:
    raise ValueError(f"Unknown model: {model}")

  for chunk in result:
    yield chunk

In [ ]:
view = gr.Interface(
    fn=stream_mode,
    inputs=[
        gr.Textbox(label="Your Message:", lines=4),
        gr.Dropdown(["GPT", "GPT-Stream", "Gemini", "Gemini-OpenAI"], label="Select Model")
    ],
    outputs=[gr.Markdown(label="Response:")],
    allow_flagging="never"
)
view.launch(share=True,debug=True)


/usr/local/lib/python3.12/dist-packages/gradio/interface.py:415: UserWarning: The `allow_flagging` parameter in `Interface` is deprecated. Use `flagging_mode` instead.
  warnings.warn(


Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://0e22f8945db89354a1.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Model used: gpt-3.5-turbo
Role - assistant
To_JSON: 
 <bound method BaseModel.to_json of ChatCompletionMessage(content='Coding is the process of using a programming language to write instructions that a computer can understand and execute. These instructions are written in the form of code, which can be used to create software, websites, applications, and more. Coding is an essential skill for computer programmers and developers, as it allows them to create and manipulate technology to meet various needs and solve problems.', refusal=None, role='assistant', annotations=[], audio=None, function_call=None, tool_calls=None)>
Model used: gemini-1.5-flash
Chunk: Coding
Chunk:  is the process of using a programming language to give instructions to a computer.  
Chunk: These instructions tell the computer what actions to perform, how to process data, and
Chunk:  what to output.  Essentially, it's writing a set of precise commands in a language the computer understands to achieve a specific ta

In [ ]:
def message_gpt_audio(prompt):
    messages = [
        {"role": "system", "content": system_message},
        {"role": "user", "content": prompt}
    ]

    completion = openai.chat.completions.create(
        model="gpt-4o-audio-preview",  # Audio-capable model
        messages=messages,
        modalities=["text", "audio"],   # Enable audio output
        audio={"voice": "alloy", "format": "wav"}  # Audio configuration
    )
    print(f"Model used: gpt-4o-audio-preview")
    # print(f"Role - {completion.choices[0].message.role}")
    # print(f"Has audio: {completion.choices[0].message.audio is not None}")

    # print(f"Content: {completion.choices[0].message.content}")
    # print(f"Audio attribute exists: {hasattr(completion.choices[0].message, 'audio')}")
    # print(f"Audio value: {completion.choices[0].message.audio}")

    # Check what attributes are available
    # print(f"Available attributes: {dir(completion.choices[0].message)}")

    return completion.choices[0].message.audio

In [ ]:
message_gpt_audio("What is coding")

Model used: gpt-4o-audio-preview
Role - assistant
Has audio: True
Content: None
Audio attribute exists: True
Audio value: ChatCompletionAudio(id='audio_68d33e4c0b548191a81b32a6f12a2ebf', data='...', expires_at=1758678108, transcript='Coding, also known as programming or software development, is the process of writing instructions for computers to follow. These instructions, known as code, are written in programming languages such as Python, Java, C++, and many others. \n\nCoding is used to create software applications, websites, games, and much more. Essentially, coding is a way for humans to communicate instructions to a computer to perform specific tasks. These tasks could range from simple calculations to complex operations like running a search engine or powering an autonomous car.\n\nBy writing code, developers build the logic that tells a computer what to do and how to do it. Without coding, the digital tools and technologies we rely on every day would not function.')
Available a

ChatCompletionAudio(id='audio_68d33e4c0b548191a81b32a6f12a2ebf', data='...', expires_at=1758678108, transcript='Coding, also known as programming or software development, is the process of writing instructions for computers to follow. These instructions, known as code, are written in programming languages such as Python, Java, C++, and many others. \n\nCoding is used to create software applications, websites, games, and much more. Essentially, coding is a way for humans to communicate instructions to a computer to perform specific tasks. These tasks could range from simple calculations to complex operations like running a search engine or powering an autonomous car.\n\nBy writing code, developers build the logic that tells a computer what to do and how to do it. Without coding, the digital tools and technologies we rely on every day would not function.')

In [ ]:
def message_gpt_audio_robust(audio_prompt):
    """
    Process audio file input and return both text and audio response
    """
    import tempfile
    import base64

    try:


        # Read and encode the input audio file
        with open(audio_prompt, "rb") as f:
            input_audio_data = base64.b64encode(f.read()).decode()

        messages = [
            {"role": "system", "content": system_message},
            {
                "role": "user",
                "content": [
                    {
                        "type": "input_audio",
                        "input_audio": {
                            "data": input_audio_data,
                            "format": "wav"  # Adjust based on your audio format
                        }
                    }
                ]
            }
        ]

        completion = openai.chat.completions.create(
            model="gpt-4o-audio-preview",
            messages=messages,
            modalities=["text", "audio"],
            audio={"voice": "alloy", "format": "wav"}
        )

        # Extract text response
        text_response = completion.choices[0].message.content
        if not text_response:
            text_response = "GPT provided audio response only"

        # Extract and handle audio response
        audio_response = completion.choices[0].message.audio

        if audio_response:

            # Debug: Check audio response type
            print(f"Audio response type: {type(audio_response)}")
            print(f"Audio response attributes: {dir(audio_response)}")

            # Handle the audio data
            if hasattr(audio_response, 'data'):
                audio_data = base64.b64decode(audio_response.data)
            else:
                audio_data = base64.b64decode(str(audio_response))

            # Handle different audio response formats # Save to temp file
            temp_file = tempfile.NamedTemporaryFile(delete=False, suffix=".wav")
            temp_file.write(audio_data)  # Now writing bytes, not string
            temp_file.close()
            audio_file_path = temp_file.name

            print(f"Audio saved to: {audio_file_path}")

        else:
            audio_file_path = None
            print("No audio response received")

        return text_response, audio_file_path

    except Exception as e:
        error_message = f"Error processing GPT audio: {str(e)}"
        print(error_message)
        return error_message, None

In [ ]:
# Alternative: Use Whisper + GPT if native audio input doesn't work
def message_gpt_audio_with_whisper(audio_prompt):
    """
    Fallback: Use Whisper to transcribe, then GPT for response
    """
    import base64
    import tempfile

    try:
        # Step 1: Transcribe audio using Whisper
        with open(audio_prompt, "rb") as audio_file:
            transcript = openai.audio.transcriptions.create(
                model="whisper-1",
                file=audio_file
            )

        user_text = transcript.text
        print(f"User said: {user_text}")

        # Step 2: Send transcribed text to GPT for audio response
        messages = [
            {"role": "system", "content": system_message},
            {"role": "user", "content": user_text}
        ]

        completion = openai.chat.completions.create(
            model="gpt-4o-audio-preview",
            messages=messages,
            modalities=["text", "audio"],
            audio={"voice": "alloy", "format": "wav"}
        )

        # Get responses
        text_response = completion.choices[0].message.content or f"You said: '{user_text}'"
        audio_response = completion.choices[0].message.audio

        # Handle audio response
        if audio_response:
            if hasattr(audio_response, 'data'):
                audio_data = base64.b64decode(audio_response.data)
            else:
                audio_data = base64.b64decode(str(audio_response))

            temp_file = tempfile.NamedTemporaryFile(delete=False, suffix=".wav")
            temp_file.write(audio_data)
            temp_file.close()
            audio_file_path = temp_file.name
        else:
            audio_file_path = None

        return text_response, audio_file_path

    except Exception as e:
        error_message = f"Error with Whisper+GPT: {str(e)}"
        print(error_message)
        return error_message, None

In [ ]:
def create_gradio_audio_interface():
    """
    Gradio interface that properly matches the function outputs
    """

    def process_audio_input(audio_input):
        if audio_input is None:
            return "Please provide audio input", None
        print(f"Received audio file: {audio_input}")

        try:
          print("Trying native GPT-4o-audio processing...")

          # Call your fixed function
          text_result, audio_result = message_gpt_audio_robust(audio_input)

          return text_result, audio_result

        except Exception as native_error:
            print(f"Native audio failed: {native_error}")

            # Fallback to Whisper + GPT
            try:
                print("Falling back to Whisper + GPT...")
                text_result, audio_result = message_gpt_audio_with_whisper(audio_input)
                return text_result, audio_result

            except Exception as whisper_error:
                print(f"Whisper fallback failed: {whisper_error}")
                return f"Both methods failed. Native: {native_error}, Whisper: {whisper_error}", None


    return gr.Interface(
        fn=process_audio_input,
        inputs=[
            gr.Audio(
                sources=["microphone", "upload"],
                type="filepath",
                label="🎤 Speak your message or upload audio file"
            )
        ],
        outputs=[
            gr.Markdown(label="GPT Text Response"),
            gr.Audio(label="GPT Audio Response")
        ],
        title="🎙️ GPT Audio Chat",
        description="Speak or upload audio, and GPT will understand and respond with both text and voice!",
        examples=[
            ["Tell me a joke"],
            ["What's the weather like?"],
            ["Explain quantum physics"]
        ]
    )

In [ ]:
create_gradio_audio_interface().launch(share=True,debug=True)

Colab notebook detected. This cell will run indefinitely so that you can see errors and logs. To turn off, set debug=False in launch().
* Running on public URL: https://56f6859b04eb8e194b.gradio.live

This share link expires in 1 week. For free permanent hosting and GPU upgrades, run `gradio deploy` from the terminal in the working directory to deploy to Hugging Face Spaces (https://huggingface.co/spaces)


Received audio file: /tmp/gradio/c5135c599cdb46e186845e5a9bb33859d8b68617df904009996679b5705f959c/audio.wav
Trying native GPT-4o-audio processing...
Audio response type: <class 'openai.types.chat.chat_completion_audio.ChatCompletionAudio'>
Audio response attributes: ['__abstractmethods__', '__annotations__', '__class__', '__class_getitem__', '__class_vars__', '__copy__', '__deepcopy__', '__delattr__', '__dict__', '__dir__', '__doc__', '__eq__', '__fields__', '__fields_set__', '__format__', '__ge__', '__get_pydantic_core_schema__', '__get_pydantic_json_schema__', '__getattr__', '__getattribute__', '__getstate__', '__gt__', '__hash__', '__init__', '__init_subclass__', '__iter__', '__le__', '__lt__', '__module__', '__ne__', '__new__', '__pretty__', '__private_attributes__', '__pydantic_complete__', '__pydantic_computed_fields__', '__pydantic_core_schema__', '__pydantic_custom_init__', '__pydantic_decorators__', '__pydantic_extra__', '__pydantic_fields__', '__pydantic_fields_set__', '__pyd